In [50]:
# better formatting for large floats
import pandas as pd
pd.options.display.float_format = "{:,.2f}".format

In [51]:
from risk.swaptions import get_swaption_portfolio
import datetime
from utils.db import dbconn
from analytics import init_ontr
import analytics
conn = dbconn('dawndb')
conn.autocommit = True
value_date = datetime.date.today()
init_ontr(value_date)

In [52]:
portf = get_swaption_portfolio(value_date, conn, source_list=["GS"])
portf

Portfolio 2020-01-24

           Product     Index       Notional    Ref Strike Direction      Type      Expiry    Vol  \
ids                                                                                                
SWPTN91   Swaption  IG33 5yr 200,000,000.00  46.59   45.0      Long  receiver  2020-02-19 40.83%   
SWPTN92   Swaption  IG33 5yr 200,000,000.00  46.59   65.0     Short     payer  2020-02-19 74.83%   
SWPTN97   Swaption  IG33 5yr 200,000,000.00  46.59   42.5      Long  receiver  2020-03-18 37.97%   
SWPTN107  Swaption  IG33 5yr 200,000,000.00  46.59   42.5      Long  receiver  2020-03-18 37.97%   
SWPTN108  Swaption  IG33 5yr 200,000,000.00  46.59   55.0     Short     payer  2020-03-18 54.38%   
SWPTN98   Swaption  IG33 5yr 200,000,000.00  46.59   57.5     Short     payer  2020-03-18 57.60%   
SWPTN93   Swaption  IG33 5yr 300,000,000.00  46.59   62.5     Short     payer  2020-03-18 63.32%   
SWPTN103  Swaption  IG33 5yr 200,000,000.00  46.59   42.5      Long  receiver  2020-04-15 39.55%   
SWPTN101  Swaption  IG33 5yr 100,000,000.00  46.58   42.5      Long  receiver  2020-04-15 39.56%   
SWPTN99   Swaption  IG33 5yr 200,000,000.00  46.58   42.5      Long  receiver  2020-04-15 39.56%   
SWPTN102  Swaption  IG33 5yr 100,000,000.00  46.58   57.5     Short     payer  2020-04-15 55.32%   
SWPTN104  Swaption  IG33 5yr 200,000,000.00  46.58   57.5     Short     payer  2020-04-15 55.32%   
SWPTN100  Swaption  IG33 5yr 200,000,000.00  46.58   60.0     Short     payer  2020-04-15 57.63%   
SWPTN110  Swaption  HY33 5yr  50,000,000.00 108.92  105.0     Short     payer  2020-04-15 48.17%   
SWPTN109  Swaption  HY33 5yr  50,000,000.00 108.92  109.5      Long  receiver  2020-04-15 28.93%   
SWPTN105  Swaption  IG33 5yr 200,000,000.00  46.58   42.5      Long  receiver  2020-05-20 41.02%   
SWPTN106  Swaption  IG33 5yr 200,000,000.00  46.58   60.0     Short     payer  2020-05-20 56.10%   

                  PV   Delta   Gamma     Theta      Vega       HY Equiv  
ids                                                                      
SWPTN91    96,319.39 -26.75%  60.60% -3,188.64  4,080.47 -15,787,111.54  
SWPTN92   -23,794.79  -7.31% -15.04%  2,128.60 -1,542.26  -4,314,115.94  
SWPTN97    63,066.05 -15.51%  36.70% -1,502.93  4,332.40  -9,151,352.04  
SWPTN107   63,066.05 -15.51%  36.70% -1,502.93  4,332.40  -9,151,352.04  
SWPTN108 -152,837.83 -30.95% -34.76%  2,916.80 -5,825.18 -18,264,316.98  
SWPTN98  -124,368.10 -25.43% -30.04%  2,793.20 -5,282.54 -15,009,920.16  
SWPTN93  -128,800.98 -17.73% -22.36%  3,702.11 -6,405.66 -15,692,360.25  
SWPTN103   95,237.93 -17.86%  30.89% -1,363.28  5,704.92 -10,542,143.17  
SWPTN101   47,737.99 -17.90%  30.92%   -682.45  2,855.09  -5,281,382.51  
SWPTN99    95,475.99 -17.90%  30.92% -1,364.90  5,710.18 -10,562,765.02  
SWPTN102 -100,969.24 -32.34% -28.64%  1,236.12 -3,680.38  -9,542,511.78  
SWPTN104 -201,938.48 -32.34% -28.64%  2,472.24 -7,360.76 -19,085,023.56  
SWPTN100 -171,842.33 -27.86% -25.74%  2,399.51 -6,871.65 -16,441,512.64  
SWPTN110 -165,874.84 -21.56%  -4.50%  2,606.42 -8,963.31 -10,777,542.75  
SWPTN109   63,201.34 -13.82%   5.98% -1,144.08  6,622.99  -6,908,992.84  
SWPTN105  127,547.56 -19.02%  25.85% -1,214.84  6,979.90 -11,222,185.16  
SWPTN106 -264,316.54 -34.57% -24.46%  2,167.00 -9,068.51 -20,398,849.70

In [53]:
df = portf._todf()
positions = df.set_index("Index")[["Delta", "Notional"]].prod(axis=1).groupby(level="Index").sum()
positions.name = 'current_delta'
gamma = df.set_index("Index")[["Gamma", "Notional"]].prod(axis=1).groupby(level="Index").sum()
gamma.name = 'gamma'

In [54]:
hedges = pd.read_sql_query("SELECT security_desc, notional FROM list_cds_positions_by_strat(%s) "
                           "WHERE folder in ('IGOPTDEL', 'HYOPTDEL')",
                           conn, params=(value_date,))

In [55]:
def f(s):
    l = s.split(" ")
    return f"{l[1]}{l[3][1:]} {l[4].lower()}r"

hedges["Index"] = hedges["security_desc"].apply(f)
hedges = hedges.rename(columns={"notional": "current hedge"})
hedges = hedges.set_index("Index")["current hedge"]
hedges = hedges.reindex(positions.index, fill_value=0.)
risk = pd.concat([hedges, positions, gamma], axis=1)
risk['net_delta'] = risk["current hedge"] + risk.current_delta
risk

current hedge   current_delta         gamma  net_delta
Index                                                           
HY33 5yr  18,500,000.00  -17,686,535.58    741,481.67 813,464.42
IG33 5yr 646,400,000.00 -645,431,240.73 61,135,754.02 968,759.27

In [56]:
portf.theta

10457.96370760693